In [1]:
%load_ext autoreload
%autoreload 2
import datasets
from joblib import Parallel, delayed
import itertools as it
from tqdm import tqdm
import sys
import spacy
import datasets
from joblib import Parallel, delayed
import itertools as it
from tqdm import tqdm
import sys
import pandas as pd
import os
import pyarrow as pa
import pyarrow.parquet as pq
import random
PATH_OUT = "data/processed/"

/home/egor/.local/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [12]:
test = datasets.load_dataset("HPLT/HPLT2.0_cleaned", "rus_Cyrl", split='train', streaming=True)

In [19]:
test_dataset = test.take(10000)

In [22]:
test_dataset_batched = test_dataset.batch(1000)
iterator = iter(test_dataset_batched)

In [23]:
b1 = next(iterator)

In [24]:
b1

{'f': ['./archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './archiveteam_archivebot_go_20220314050001/doc.rt.com-inf-20220307-230755-3t8a6-00162.warc.gz',
  './

In [45]:
import datasets
from joblib import Parallel, delayed
import itertools as it
from tqdm import tqdm
import sys
import pandas as pd
import os
import pyarrow as pa
import pyarrow.parquet as pq
import random
import argparse
from lang_funcs import lang_to_func
import re

#all lower case
#get rid of punctuation?
#lemmatize the keywords
#input is a dictionary ("text": )
#write one function for each language
#comparing function extra?
#output: true or false (edited) 

# TODO: add command line arguments for language, batch size and proportion of data

BATCH_SIZE = 1000
lang = "rus_Cyrl" # TODO remove
chunk_ind = 0 # TODO remove
chunk_size = 10000 # TODO remove

PATH_OUT = "data/processed/"
os.makedirs(PATH_OUT, exist_ok=True)

lang_func_norm = lang_to_func(lang)

lang_to_keycol = {
    "rus_Cyrl": "Russian",
    "eng_Latn" : "English",
    "fin_Latn" : "Finnish",
    "zho_Hans" : "Chinese",
    "deu_Latn" : "German",
    "ben_Beng" : "Bangla",
    "hin_Deva" : "Hindi"
            }
# Read the key csv
# Normalize the keys in the list

keywords_df = pd.read_csv('keywords.csv')  

lang_keywords = keywords_df[lang_to_keycol[lang]].dropna()
keywords = [lang_func_norm(word) for word in lang_keywords]

# TODO word by word matching
def compare_funct(text):
    text = lang_func_norm(text)
    split_text = text.split(" ")
    sets = {}
    for word in keywords:
        words = word.split(" ")
        w_len = len(words)
        if w_len not in sets.keys():
            sets[w_len] = set([" ".join(split_text[i:i+w_len]) for i in range(len(split_text)-w_len+1)])
        if word in sets[w_len]:
            return True
    return False

# dataset_orig = datasets.load_dataset("HPLT/HPLT2.0_cleaned", lang, split='train', streaming=True)
dataset = dataset_orig.skip(chunk_ind * chunk_size).take(chunk_size)
dataset_batched = dataset.batch(BATCH_SIZE)

def process_batch(batch_index: int, batch: dict) -> int:
    # Process batch
    texts = batch["text"]
    mask = [compare_funct(text) for text in texts]
    for key in batch.keys():
        batch[key] = [batch[key][i] for i in range(len(batch[key])) if mask[i]]
    table = pa.Table.from_pydict(batch)
    pq.write_table(table, f"{PATH_OUT}{chunk_ind}_{batch_index}.parquet")
    return batch_index

iterator = iter(dataset_batched)

parallel = Parallel(n_jobs=-1) # TODO: config backend

# Launch the processing
parallel(delayed(process_batch)(i, batch) for i, batch in tqdm(enumerate(iterator)))

10it [00:16,  1.70s/it]


[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]

In [46]:
table = pq.ParquetFile(f"{PATH_OUT}{chunk_ind}_{2}.parquet")
table_df = table.read().to_pandas()

In [47]:
len(table_df)

40

In [48]:
text = table_df["text"].iloc[2]
norm_text = lang_func_norm(text)

In [49]:
# Find the keywords in the text
for word in keywords:
    window_size = len(word)
    i = 0
    while i < len(text):
        if norm_text[i:i + window_size] == word:
            print(f"Found {word} at index {i}")
        i += 1

Found карьер at index 2835


In [50]:
norm_text

'закончить месяц по санитарный очистка и благоустройство населённый место , провести значительный работа : повсеместно пройти субботник , ликвидироваться стихийный мусорный свалка , осуществляться освежать покраска забор , фундамент , фасад здание , проводиться ямочный ремонт улица и дорога . \n но , вместе с тем , несмотря на положительный результат месячник , работник воложинского центр гигиена и эпидемиология продолжать фиксироваться и негативный момент , отмечаться многочисленный недостаток . \n не в весь сельисполкомах провести должный работа по вовлечение предприятие , организация , население в работа по очистка территория , приведение в должный санитарный состояние кладбище . если в саковщинском сельисполкоме проводиться ежедневный работа в это направление , то в яршевическом , раковском , пряльницком сельсовет видно много отрицательный пример . \n т 1000 ак , в пряльницком сельисполкоме ( председатель - щасновская о.е . ) на кладбище в д.яршевичи контейнерный площадка должный о

In [56]:
norm_text[4850:]

'работка урановый месторождение , проектирование , строительство и эксплуатация легководный реактор , переработка и обращение с радиоактивный отход . \n соглашение , подписать 12 май 2009 год в токио , было заключить на 25 год . после истечение этот срок оно оставаться в сила , пока одна из сторона не захотеть разорвать его , пояснять агентство . \n также депутат рассмотреть проект закон о ратификация соглашение с монголия о создание совместный компания с ограничить ответственность " дорнод уран " . \n депутат обсудить вопрос , связать с детский сад и страхование автовладелец \n возвращаться к блок внутренний тема , депутат в второй чтение обсудить правительственный поправка к закон " об образование " , которые предусматривать материальный поддержка для родитель ребёнок , посещать государственный и муниципальный дошкольный учреждение . как пояснить глава комитет по образование григорий балыхин , предлагаться предоставить субъект рф право самостоятельно определять размер компенсация час

In [42]:
from lang_funcs import lang_to_func
lang_func_norm = lang_to_func(lang)

In [40]:
len(text)

3246

In [43]:
%timeit lang_func_norm(text)

92.3 ms ± 2.73 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [79]:
text.translate(str.maketrans('', '', string.punctuation))

'Компания Sony официально анонсировала плеер слухи о котором в последнее время не давали спокойно спать многим фанатам гаджетов катающийся ушастый бочонок Rolly Официальное название модели  SEP10BT она представляет собой плеер который может танцевать под музыку и ездить по заученной траектории\nSony позиционирует устройство как продукт для всей семьи В данном случае это можно понимать так что Rolly больше игрушка чем плеер Тем более что начинка у него по нынешним временам очень скромная проигрывание музыки осуществляется либо с внутренней памяти 1 Гб либо по интерфейсу Bluetooth 20 A2DP и AVRCP Интерфейс USB стандартно используется для перекачки аудиофайлов и для подзарядки\nЗато антураж у новинки которая поступит в продажу в Японии 29 сентября по цене в 354 доллара очень оригинальный На корпусе присутствуют только две кнопки предназначенные для включения и для запуска воспроизведения а всё остальное управление осуществляется вращением двух колец на которых Rolly предвигается\nОтсутств

In [16]:
from lang_funcs import lang_to_func

In [51]:
import time

In [54]:
time.strftime("%H:%M:%S", time.localtime())

'23:47:06'